# Install and import dependencies

In [ ]:
!pip install tensorflow opencv-python mediapipe sklearn matplotlib pydot PyLaTeX latex wandb

In [1]:
import cv2 # OpenCV
import numpy as np
import os # For manipulating directory
from matplotlib import pyplot as plt
import time
import mediapipe as mp
from sklearn.model_selection import train_test_split
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Sequential # Sequential model
from tensorflow.keras.layers import LSTM, Dense, Dropout # Layers name
from tensorflow.keras.optimizers import Adam, Nadam
from tensorflow.keras.utils import plot_model
from sklearn.metrics import confusion_matrix, multilabel_confusion_matrix, accuracy_score, classification_report
import seaborn as sns # Matrics visualization
import itertools
import wandb
from wandb.keras import WandbCallback
import pprint

# Login W&B

In [2]:
wandb.login()

wandb: Currently logged in as: ichsanarsyi (use `wandb login --relogin` to force relogin)


True

# Visualize dataset distribution

In [ ]:
#Visualize data distribution per class
action_class = ["run", "walk", "skip", "jack", "jump", "pjump", "side", "wave2", "wave1", "bend"]
nvideo = [10, 10, 10, 9, 9, 9, 9, 9, 9, 9]
#font
plt.rcParams['font.family'] = 'serif'
plt.rcParams['font.serif'] = ['Times New Roman']
plt.rcParams.update({'font.size': 12})
#plot
fig, ax = plt.subplots(figsize=(6, 4))
_ = plt.xticks(rotation=45)
_ = plt.grid(which="major", axis="y", zorder=0)
_ = ax.set(title="Jumlah Video per Kelas pada Dataset Weizmann", yticks=[0,1,2,3,4,5,6,7,8,9,10])
barplot = ax.bar(action_class, nvideo, zorder=3, color="lightsteelblue")
#_ = ax.bar_label(barplot, label_type="center")
#save plot
#plt.savefig("graphdatasetlegacy.png", dpi=96, orientation="landscape", format="png", transparent=True)

In [ ]:
#Visualize data split after augmentation
action_class = np.arange(10)
nvideo_train = [27, 27, 27, 27, 27, 27, 27, 27, 27, 27]
nvideo_valid = [9, 9, 9, 9, 9, 9, 9, 9, 9, 9] 
nvideo_test = [9, 9, 9, 9, 9, 9, 9, 9, 9, 9]
width = 0.3
#plot
fig, ax = plt.subplots(figsize=(12, 6.75))
_ = plt.xticks(action_class,
               ["run", "walk", "skip", "jack", "jump", "pjump", "side", "wave2", "wave1", "bend"],
               rotation=0)
_ = plt.grid(which="major", axis="y", zorder=0)
_ = ax.set(title="Jumlah Video per Kelas pada Dataset Weizmann Hasil Data Augmentation", yticks=[0,5,9,10,15,20,25,27,30])
barplot1 = ax.bar(action_class-width, nvideo_train, width, zorder=3, color="salmon")
barplot2 = ax.bar(action_class, nvideo_valid, width, zorder=3, color="lightgreen")
barplot3 = ax.bar(action_class+width, nvideo_test, width, zorder=3, color="skyblue")
_ = ax.bar_label(barplot1, label_type="center")
_ = ax.bar_label(barplot2, label_type="center")
_ = ax.bar_label(barplot3, label_type="center")
_ = ax.legend(["training", "validation", "testing"])
#save plot
#plt.savefig("graphdatasetaug.png", dpi=96, orientation="landscape", format="png", transparent=True)

# Function initialization

In [3]:
mp_pose = mp.solutions.pose # Pose model
mp_drawing = mp.solutions.drawing_utils # Drawing utilities
mp_connections = mp.solutions.pose_connections # Pose Connections

In [4]:
def mediapipe_detection(image, model):
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB) # Convert BGR to RGB
    image.flags.writeable = False # Image is unwritable
    results = model.process(image) # Prediction
    image.flags.writeable = True # Image is writeable
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR) # Convert RGB to BGR
    return image, results

def draw_landmarks(image, results):
    mp_drawing.draw_landmarks(image,
                              results.pose_landmarks,
                              mp_pose.POSE_CONNECTIONS)
    
def draw_styled_landmarks(image, results):
    mp_drawing.draw_landmarks(image,
                              results.pose_landmarks,
                              mp_pose.POSE_CONNECTIONS,
                              mp_drawing.DrawingSpec(color=(80,110,10),
                                                     thickness=1,
                                                     circle_radius=1),
                              mp_drawing.DrawingSpec(color=(80,255,121),
                                                     thickness=1,
                                                     circle_radius=1))
    
def extract_keypoints(results):
    pose = np.array([[res.x, res.y, res.y, res.visibility] for res in results.pose_landmarks.landmark]).flatten() if results.pose_landmarks else np.zeros(4*33)
    return pose

def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title="Confusion Matrix",
                          cmap=plt.cm.Blues):
    """
    Prints & plots confusion matrix.
    Normalization can be applied by setting "normalize=True".
    """
    plt.imshow(cm, interpolation="nearest", cmap=cmap)
    plt.title(title)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=45)
    plt.yticks(tick_marks, classes)
    
    if normalize:
        cm = cm.astype("float") / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print("Confusion matrix, without normalization")
        
    print(cm)
    
    thresh = cm.max() / 2.
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plt.text(j, i, cm[i, j],
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black")
        
    plt.tight_layout()
    plt.ylabel("True label")
    plt.xlabel("Predicted label")

# Base variables

In [5]:
# Path for exporting data in numpy array format
DATA_PATH = os.path.join("dataset_weizmann450_trainvalidtest_mp")

# Action to detect
actions = np.array(["run", "walk", "skip", "jack", "jump", "pjump", "side", "wave2", "wave1", "bend"])

# Data role
roles = np.array(["train", "valid", "test"])

# 27 videos per action for training
no_sequences_train = 27

# 9 videos per action for validation
no_sequences_valid = 9

# 9 videos per action for testing
no_sequences_test = 9

# frame length
sequence_length = 25

In [ ]:
actions.shape[0]

# Collecting MediaPipe:Pose keypoints

In [ ]:
# Make folder for saving landmarks/keypoints data

for role in roles:
    if role == "train":
        for action in actions:
            for sequence_train in range(no_sequences_train):
                try:
                    os.makedirs(os.path.join(DATA_PATH, role, action, str(sequence_train)))
                except:
                    pass
    elif role == "valid":
        for action in actions:
            for sequence_valid in range(no_sequences_valid):
                try:
                    os.makedirs(os.path.join(DATA_PATH, role, action, str(sequence_valid)))
                except:
                    pass
    else:
        for action in actions:
            for sequence_test in range(no_sequences_test):
                try:
                    os.makedirs(os.path.join(DATA_PATH, role, action, str(sequence_test)))
                except:
                    pass

In [ ]:
# Play video input simultaneously & try to collect keypoints values
# for train, valid, & test folder

with mp_pose.Pose(static_image_mode=False,
                  model_complexity=1,
                  smooth_landmarks=True,
                  enable_segmentation=False,
                  smooth_segmentation=True,
                  min_detection_confidence=0.5,
                  min_tracking_confidence=0.5) as pose:
    
    for role in roles:
        if role == "train":
            for action in actions:
                for sequence_train in range(no_sequences_train):
                    cap = cv2.VideoCapture("dataset_weizmann450_trainvalidtest_encode/{}/{}/{}.avi".format(role,
                                                                                                           action, 
                                                                                                           sequence_train))
                    for frame_num in range(sequence_length):
                        # Read feed
                        ret, frame = cap.read()
                        # Make detections
                        image, results = mediapipe_detection(frame, pose)
                        print(results)
                        # Draw landmarks
                        draw_styled_landmarks(image, results)
                        # Export keypoints
                        keypoints = extract_keypoints(results)
                        npy_path = os.path.join(DATA_PATH, role, action, str(sequence_train), str(frame_num))
                        np.save(npy_path, keypoints)
                        # Show to screen
                        cv2.imshow("OpenCV Feed", image)
                        # Break while loop
                        if cv2.waitKey(10) & 0xFF == ord("q"):
                            break
                    cap.release()
                cv2.destroyAllWindows()
                
        elif role == "valid":
            for action in actions:
                for sequence_valid in range(no_sequences_valid):
                    cap = cv2.VideoCapture("dataset_weizmann450_trainvalidtest_encode/{}/{}/{}.avi".format(role,
                                                                                                           action,
                                                                                                           sequence_valid))
                    for frame_num in range(sequence_length):
                        # Read feed
                        ret, frame = cap.read()
                        # Make detections
                        image, results = mediapipe_detection(frame, pose)
                        print(results)
                        # Draw landmarks
                        draw_styled_landmarks(image, results)
                        # Export keypoints
                        keypoints = extract_keypoints(results)
                        npy_path = os.path.join(DATA_PATH, role, action, str(sequence_valid), str(frame_num))
                        np.save(npy_path, keypoints)
                        # Show to screen
                        cv2.imshow("OpenCV Feed", image)
                        # Break while loop
                        if cv2.waitKey(10) & 0xFF == ord("q"):
                            break
                    cap.release()
                cv2.destroyAllWindows()
                
        else:
            for action in actions:
                for sequence_test in range(no_sequences_test):
                    cap = cv2.VideoCapture("dataset_weizmann450_trainvalidtest_encode/{}/{}/{}.avi".format(role,
                                                                                                           action,
                                                                                                           sequence_test))
                    for frame_num in range(sequence_length):
                        # Read feed
                        ret, frame = cap.read()
                        # Make detections
                        image, results = mediapipe_detection(frame, pose)
                        print(results)
                        # Draw landmarks
                        draw_styled_landmarks(image, results)
                        # Export keypoints
                        keypoints = extract_keypoints(results)
                        npy_path = os.path.join(DATA_PATH, role, action, str(sequence_test), str(frame_num))
                        np.save(npy_path, keypoints)
                        # Show to screen
                        cv2.imshow("OpenCV Feed", image)
                        # Break while loop
                        if cv2.waitKey(10) & 0xFF == ord("q"):
                            break
                    cap.release()
                cv2.destroyAllWindows()

# Labelling data

In [6]:
label_map = {label:num for num, label in enumerate(actions)}
label_map

{'run': 0,
 'walk': 1,
 'skip': 2,
 'jack': 3,
 'jump': 4,
 'pjump': 5,
 'side': 6,
 'wave2': 7,
 'wave1': 8,
 'bend': 9}

In [7]:
# Labelling each sequence/class
sequences_train, labels_train = [], []
sequences_valid, labels_valid = [], []
sequences_test, labels_test = [], []

for role in roles:
    if role == "train":
        for action in actions:
            for sequence_train in range(no_sequences_train):
                window = []
                for frame_num in range(sequence_length):
                    res = np.load(os.path.join(DATA_PATH, role, action, str(sequence_train), "{}.npy".format(frame_num)))
                    window.append(res)
                sequences_train.append(window)
                labels_train.append(label_map[action])
    elif role == "valid":
        for action in actions:
            for sequence_valid in range(no_sequences_valid):
                window = []
                for frame_num in range(sequence_length):
                    res = np.load(os.path.join(DATA_PATH, role, action, str(sequence_valid), "{}.npy".format(frame_num)))
                    window.append(res)
                sequences_valid.append(window)
                labels_valid.append(label_map[action])
    else:
        for action in actions:
            for sequence_test in range(no_sequences_test):
                window = []
                for frame_num in range(sequence_length):
                    res = np.load(os.path.join(DATA_PATH, role, action, str(sequence_test), "{}.npy".format(frame_num)))
                    window.append(res)
                sequences_test.append(window)
                labels_test.append(label_map[action])

In [8]:
X_train = np.array(sequences_train)
X_valid = np.array(sequences_valid)
X_test = np.array(sequences_test)

y_train = to_categorical(labels_train).astype(int)
y_valid = to_categorical(labels_valid).astype(int)
y_test = to_categorical(labels_test).astype(int)

print("X_train shape : "+str(X_train.shape))
print("X_valid shape : "+str(X_valid.shape))
print("X_test shape : "+str(X_test.shape))
print("y_train shape : "+str(y_train.shape))
print("y_valid shape : "+str(y_valid.shape))
print("y_test shape : "+str(y_test.shape))

# X shape = (data, frame, keypoint)
# keypoint = 33 keypoints * 4 values (3 axis[x,y,z] + visibility) = 132

# y shape = (data, label)

X_train shape : (270, 25, 132)
X_valid shape : (90, 25, 132)
X_test shape : (90, 25, 132)
y_train shape : (270, 10)
y_valid shape : (90, 10)
y_test shape : (90, 10)


# Illustrate extracting keypoints process
for report only

In [ ]:
# Visualize extracting keypoints process

cap = cv2.VideoCapture("dataset_weizmann450\jack\denis_jack_3.avi") # Video File

# Set mediapipe model
with mp_pose.Pose(static_image_mode=False,
                  model_complexity=1,
                  smooth_landmarks=True,
                  enable_segmentation=False,
                  smooth_segmentation=True,
                  min_detection_confidence=0.5,
                  min_tracking_confidence=0.5) as pose:
    while cap.isOpened():
        
        # Read feed
        ret, frame = cap.read()
        
        # Make detections
        image, results = mediapipe_detection(frame, pose)
        print(results)
        
        # Draw landmarks
        draw_styled_landmarks(image, results)
        
        # Show to screen
        cv2.imshow("OpenCV Feed", image)
        
        # Break while loop
        if cv2.waitKey(10) & 0xFF == ord("q"):
            break
    
    cap.release()
    cv2.destroyAllWindows()


In [ ]:
plt.figure()
plt.imshow(image)

In [ ]:
# Locate log folder for monitoring with TensorBoard
#log_dir = os.path.join("Logs")
#tb_callback = TensorBoard(log_dir=log_dir)

# W&B Monitoring

In [ ]:
# for monitoring single config only

# wandb.init(project="HAR_MP_LSTM_TugasAkhir_Ichsan",
#            entity="ichsanarsyi",
#            config={
#                "learning_rate" : 0.0001,
#                "batch_size" : 4,
#                "epochs" : 200,
#                "loss_function" : "categorical_crossentropy",
#                "architecture" : "LSTM",
#                "dataset" : "weizmann450"               
#            })
# config = wandb.config

In [9]:
# sweep config
sweep_config = {
    'method' : 'grid' 
}

In [10]:
# additional metric
metric = {
    'name' : 'loss', # try use val_loss instead
    'goal' : 'minimize'
}
sweep_config['metric'] = metric

In [11]:
# hyperparameters dictionary
parameters_dict = {
    'batch_size' : {
        'values' : [4, 8, 16]
    },
    'learning_rate' : {
        'values' : [0.0001, 0.000015]
    },
    'epochs' : {
        'values' : [200, 500]
    },
    'dropout' : {
        'values' : [0, 0.25, 0.5]
    },
    'recurrent_dropout' : {
        'values' : [0, 0.25, 0.5]
    }
}
sweep_config['parameters'] = parameters_dict

In [12]:
pprint.pprint(sweep_config)

{'method': 'grid',
 'metric': {'goal': 'minimize', 'name': 'loss'},
 'parameters': {'batch_size': {'values': [4, 8, 16]},
                'dropout': {'values': [0, 0.25, 0.5]},
                'epochs': {'values': [200, 500]},
                'learning_rate': {'values': [0.0001, 1.5e-05]},
                'recurrent_dropout': {'values': [0, 0.25, 0.5]}}}


In [13]:
sweep_id = wandb.sweep(sweep_config, project="HAR_MP_LSTM_TugasAkhir_TestSweep1_Ichsan")

Create sweep with ID: p5bh8rh2
Sweep URL: https://wandb.ai/ichsanarsyi/HAR_MP_LSTM_TugasAkhir_TestSweep1_Ichsan/sweeps/p5bh8rh2


In [14]:
def train():
    # Default values for hyper-parameters we're going to sweep over
    config_defaults = {
        'batch_size': 4,
        'learning_rate': 0.0001,
        'epochs': 200,
        'dropout': 0,
        'recurrent_dropout': 0
    }

    # Initialize a new wandb run
    wandb.init(config=config_defaults)
    
    # Config is a variable that holds and saves hyperparameters and inputs
    config = wandb.config
    
    # Define the model architecture
    lstm2_dense2_d_rd_nadam = Sequential([
        LSTM(128, dropout=config.dropout,
             recurrent_dropout=config.recurrent_dropout,
             return_sequences=True, input_shape=(25,132)),
        LSTM(64, dropout=config.dropout,
             recurrent_dropout=config.recurrent_dropout,
             return_sequences=False),
        Dense(32, activation="relu"),
        Dense(actions.shape[0], activation="softmax")
    ])

    # Compile model with learning rate
    lstm2_dense2_d_rd_nadam.compile(Nadam(learning_rate=config.learning_rate),
                                          loss="categorical_crossentropy",
                                          metrics=["categorical_accuracy"])
    
    # Train model
    lstm2_dense2_d_rd_nadam.fit(X_train, y_train,
                                batch_size=config.batch_size,
                                epochs=config.epochs,
                                shuffle=True, verbose=2,
                                validation_data=(X_valid, y_valid),
                                callbacks=[WandbCallback()])

In [15]:
# Run the sweep agent
wandb.agent(sweep_id, train)

wandb: Agent Starting Run: h7z270n0 with config:
wandb: 	batch_size: 4
wandb: 	dropout: 0
wandb: 	epochs: 200
wandb: 	learning_rate: 0.0001
wandb: 	recurrent_dropout: 0


Epoch 1/200
68/68 - 16s - loss: 2.2756 - categorical_accuracy: 0.1519 - val_loss: 2.2011 - val_categorical_accuracy: 0.2667 - _timestamp: 1647784901.0000 - _runtime: 40.0000 - 16s/epoch - 240ms/step
Epoch 2/200
68/68 - 3s - loss: 2.1109 - categorical_accuracy: 0.2630 - val_loss: 1.9906 - val_categorical_accuracy: 0.3333 - _timestamp: 1647784904.0000 - _runtime: 43.0000 - 3s/epoch - 39ms/step
Epoch 3/200
68/68 - 4s - loss: 1.9179 - categorical_accuracy: 0.3111 - val_loss: 1.8384 - val_categorical_accuracy: 0.3444 - _timestamp: 1647784906.0000 - _runtime: 45.0000 - 4s/epoch - 53ms/step
Epoch 4/200
68/68 - 3s - loss: 1.7634 - categorical_accuracy: 0.3667 - val_loss: 1.7466 - val_categorical_accuracy: 0.2778 - _timestamp: 1647784910.0000 - _runtime: 49.0000 - 3s/epoch - 40ms/step
Epoch 5/200
68/68 - 3s - loss: 1.6091 - categorical_accuracy: 0.3963 - val_loss: 1.5457 - val_categorical_accuracy: 0.4556 - _timestamp: 1647784913.0000 - _runtime: 52.0000 - 3s/epoch - 39ms/step
Epoch 6/200
68/68

Epoch 43/200
68/68 - 2s - loss: 0.2497 - categorical_accuracy: 0.9296 - val_loss: 0.6530 - val_categorical_accuracy: 0.7444 - _timestamp: 1647785014.0000 - _runtime: 153.0000 - 2s/epoch - 35ms/step
Epoch 44/200
68/68 - 2s - loss: 0.2684 - categorical_accuracy: 0.9148 - val_loss: 0.7750 - val_categorical_accuracy: 0.7667 - _timestamp: 1647785016.0000 - _runtime: 155.0000 - 2s/epoch - 35ms/step
Epoch 45/200
68/68 - 2s - loss: 0.2644 - categorical_accuracy: 0.9185 - val_loss: 0.7426 - val_categorical_accuracy: 0.6778 - _timestamp: 1647785018.0000 - _runtime: 157.0000 - 2s/epoch - 35ms/step
Epoch 46/200
68/68 - 2s - loss: 0.2300 - categorical_accuracy: 0.9444 - val_loss: 0.6430 - val_categorical_accuracy: 0.7222 - _timestamp: 1647785021.0000 - _runtime: 160.0000 - 2s/epoch - 36ms/step
Epoch 47/200
68/68 - 2s - loss: 0.2408 - categorical_accuracy: 0.9222 - val_loss: 0.7096 - val_categorical_accuracy: 0.7000 - _timestamp: 1647785023.0000 - _runtime: 162.0000 - 2s/epoch - 35ms/step
Epoch 48/2

Epoch 85/200
68/68 - 2s - loss: 0.2546 - categorical_accuracy: 0.9037 - val_loss: 0.6458 - val_categorical_accuracy: 0.7667 - _timestamp: 1647785118.0000 - _runtime: 257.0000 - 2s/epoch - 34ms/step
Epoch 86/200
68/68 - 2s - loss: 0.2185 - categorical_accuracy: 0.9037 - val_loss: 0.7798 - val_categorical_accuracy: 0.7222 - _timestamp: 1647785120.0000 - _runtime: 259.0000 - 2s/epoch - 34ms/step
Epoch 87/200
68/68 - 2s - loss: 0.1422 - categorical_accuracy: 0.9630 - val_loss: 0.6374 - val_categorical_accuracy: 0.7333 - _timestamp: 1647785123.0000 - _runtime: 262.0000 - 2s/epoch - 34ms/step
Epoch 88/200
68/68 - 2s - loss: 0.0973 - categorical_accuracy: 0.9704 - val_loss: 0.5691 - val_categorical_accuracy: 0.7889 - _timestamp: 1647785125.0000 - _runtime: 264.0000 - 2s/epoch - 35ms/step
Epoch 89/200
68/68 - 2s - loss: 0.0902 - categorical_accuracy: 0.9852 - val_loss: 0.6176 - val_categorical_accuracy: 0.7444 - _timestamp: 1647785127.0000 - _runtime: 266.0000 - 2s/epoch - 35ms/step
Epoch 90/2

Epoch 127/200
68/68 - 2s - loss: 0.0623 - categorical_accuracy: 0.9815 - val_loss: 0.7601 - val_categorical_accuracy: 0.7556 - _timestamp: 1647785219.0000 - _runtime: 358.0000 - 2s/epoch - 36ms/step
Epoch 128/200
68/68 - 2s - loss: 0.0276 - categorical_accuracy: 1.0000 - val_loss: 0.8220 - val_categorical_accuracy: 0.7889 - _timestamp: 1647785221.0000 - _runtime: 360.0000 - 2s/epoch - 34ms/step
Epoch 129/200
68/68 - 2s - loss: 0.1173 - categorical_accuracy: 0.9630 - val_loss: 1.2101 - val_categorical_accuracy: 0.6889 - _timestamp: 1647785223.0000 - _runtime: 362.0000 - 2s/epoch - 35ms/step
Epoch 130/200
68/68 - 2s - loss: 0.2007 - categorical_accuracy: 0.9519 - val_loss: 0.7097 - val_categorical_accuracy: 0.7444 - _timestamp: 1647785226.0000 - _runtime: 365.0000 - 2s/epoch - 36ms/step
Epoch 131/200
68/68 - 2s - loss: 0.0852 - categorical_accuracy: 0.9704 - val_loss: 0.7720 - val_categorical_accuracy: 0.7778 - _timestamp: 1647785228.0000 - _runtime: 367.0000 - 2s/epoch - 34ms/step
Epoch

...

Epoch 372/500
17/17 - 7s - loss: 1.0364 - categorical_accuracy: 0.6111 - val_loss: 0.9369 - val_categorical_accuracy: 0.5556 - _timestamp: 1647968694.0000 - _runtime: 1646.0000 - 7s/epoch - 422ms/step
Epoch 373/500
17/17 - 4s - loss: 0.9797 - categorical_accuracy: 0.6630 - val_loss: 0.9052 - val_categorical_accuracy: 0.5889 - _timestamp: 1647968698.0000 - _runtime: 1650.0000 - 4s/epoch - 260ms/step
Epoch 374/500
17/17 - 5s - loss: 1.0313 - categorical_accuracy: 0.6037 - val_loss: 0.8616 - val_categorical_accuracy: 0.6444 - _timestamp: 1647968703.0000 - _runtime: 1655.0000 - 5s/epoch - 310ms/step
Epoch 375/500
17/17 - 5s - loss: 1.0269 - categorical_accuracy: 0.6370 - val_loss: 0.8644 - val_categorical_accuracy: 0.6444 - _timestamp: 1647968709.0000 - _runtime: 1661.0000 - 5s/epoch - 321ms/step
Epoch 376/500
17/17 - 4s - loss: 1.0171 - categorical_accuracy: 0.6259 - val_loss: 0.8785 - val_categorical_accuracy: 0.6000 - _timestamp: 1647968713.0000 - _runtime: 1665.0000 - 4s/epoch - 236ms/

Epoch 413/500
17/17 - 4s - loss: 0.9906 - categorical_accuracy: 0.6407 - val_loss: 0.8169 - val_categorical_accuracy: 0.6556 - _timestamp: 1647968863.0000 - _runtime: 1815.0000 - 4s/epoch - 247ms/step
Epoch 414/500
17/17 - 4s - loss: 0.9652 - categorical_accuracy: 0.6593 - val_loss: 0.8513 - val_categorical_accuracy: 0.6444 - _timestamp: 1647968867.0000 - _runtime: 1819.0000 - 4s/epoch - 229ms/step
Epoch 415/500
17/17 - 4s - loss: 0.9829 - categorical_accuracy: 0.6185 - val_loss: 0.8398 - val_categorical_accuracy: 0.6333 - _timestamp: 1647968871.0000 - _runtime: 1823.0000 - 4s/epoch - 253ms/step
Epoch 416/500
17/17 - 5s - loss: 0.9529 - categorical_accuracy: 0.6296 - val_loss: 0.8339 - val_categorical_accuracy: 0.6333 - _timestamp: 1647968876.0000 - _runtime: 1828.0000 - 5s/epoch - 267ms/step
Epoch 417/500
17/17 - 6s - loss: 0.9195 - categorical_accuracy: 0.6815 - val_loss: 0.8223 - val_categorical_accuracy: 0.6667 - _timestamp: 1647968882.0000 - _runtime: 1834.0000 - 6s/epoch - 355ms/

Epoch 454/500
17/17 - 4s - loss: 0.9505 - categorical_accuracy: 0.6444 - val_loss: 0.8277 - val_categorical_accuracy: 0.6000 - _timestamp: 1647969040.0000 - _runtime: 1992.0000 - 4s/epoch - 230ms/step
Epoch 455/500
17/17 - 4s - loss: 0.9784 - categorical_accuracy: 0.6296 - val_loss: 0.8165 - val_categorical_accuracy: 0.6333 - _timestamp: 1647969044.0000 - _runtime: 1996.0000 - 4s/epoch - 226ms/step
Epoch 456/500
17/17 - 4s - loss: 0.9001 - categorical_accuracy: 0.6630 - val_loss: 0.8059 - val_categorical_accuracy: 0.6444 - _timestamp: 1647969048.0000 - _runtime: 2000.0000 - 4s/epoch - 251ms/step
Epoch 457/500
17/17 - 4s - loss: 0.9714 - categorical_accuracy: 0.6259 - val_loss: 0.7953 - val_categorical_accuracy: 0.6667 - _timestamp: 1647969052.0000 - _runtime: 2004.0000 - 4s/epoch - 263ms/step
Epoch 458/500
17/17 - 4s - loss: 0.9311 - categorical_accuracy: 0.6519 - val_loss: 0.8068 - val_categorical_accuracy: 0.6444 - _timestamp: 1647969057.0000 - _runtime: 2009.0000 - 4s/epoch - 250ms/

Epoch 495/500
17/17 - 5s - loss: 0.9091 - categorical_accuracy: 0.6852 - val_loss: 0.7836 - val_categorical_accuracy: 0.6556 - _timestamp: 1647969209.0000 - _runtime: 2161.0000 - 5s/epoch - 273ms/step
Epoch 496/500
17/17 - 5s - loss: 0.8525 - categorical_accuracy: 0.6926 - val_loss: 0.7970 - val_categorical_accuracy: 0.6444 - _timestamp: 1647969213.0000 - _runtime: 2165.0000 - 5s/epoch - 276ms/step
Epoch 497/500
17/17 - 4s - loss: 0.9023 - categorical_accuracy: 0.6889 - val_loss: 0.7748 - val_categorical_accuracy: 0.6333 - _timestamp: 1647969217.0000 - _runtime: 2169.0000 - 4s/epoch - 231ms/step
Epoch 498/500
17/17 - 4s - loss: 0.9610 - categorical_accuracy: 0.6444 - val_loss: 0.7644 - val_categorical_accuracy: 0.6444 - _timestamp: 1647969221.0000 - _runtime: 2173.0000 - 4s/epoch - 262ms/step
Epoch 499/500
17/17 - 5s - loss: 0.8420 - categorical_accuracy: 0.6815 - val_loss: 0.7536 - val_categorical_accuracy: 0.6556 - _timestamp: 1647969227.0000 - _runtime: 2179.0000 - 5s/epoch - 305ms/

wandb: Sweep Agent: Waiting for job.
wandb: Sweep Agent: Exiting.


# Dropout layer added below

# lstm2_dense2_rd2_lr5_e1k_b16
lstm2 (128,64) + dense2 (32,10) + activation=default + nadam + epochs=1000 + recurrent_dropout=0.2 + lr=0.00001 + batch=16 -> vairly good curve, good diverse
#### candidate

In [ ]:
# Define a sequential model
lstm2_dense2_rd2_lr5_e1k_b16 = Sequential([
    LSTM(128, recurrent_dropout=0.2, return_sequences=True, input_shape=(25,132)),
    LSTM(64, recurrent_dropout=0.2, return_sequences=False),
    Dense(32, activation="relu"),
    Dense(actions.shape[0], activation="softmax")
])

In [ ]:
# Compile model with learning rate
lstm2_dense2_rd2_lr5_e1k_b16.compile(Nadam(learning_rate=0.00001),
                                            loss="categorical_crossentropy",
                                            metrics=["categorical_accuracy"])

In [ ]:
# Training model with validation
history = lstm2_dense2_rd2_lr5_e1k_b16.fit(X_train, y_train, batch_size=16, epochs=1000, shuffle=True, verbose=2,
                                                  validation_data=(X_valid, y_valid))

In [ ]:
lstm2_dense2_rd2_lr5_e1k_b16.summary()

In [ ]:
# Save Model
lstm2_dense2_rd2_lr5_e1k_b16.save("lstm2_dense2_rd2_lr5_e1k_b16_1601_18032022.h5")

In [ ]:
# Load Model
lstm2_dense2_rd2_lr5_e1k_b16.load_weights("lstm2_dense2_rd2_lr5_e1k_b16_1601_18032022.h5")

In [ ]:
# Visualize
plot_model(lstm2_dense2_rd2_lr5_e1k_b16, to_file = "arc_lstm2_dense2_rd2_lr5_e1k_b16_1601_18032022.png", show_shapes = True)

In [ ]:
# Plot training and validation

loss = history.history["loss"]
val_loss = history.history["val_loss"]
epochs = range(1, len(loss) + 1)
plt.plot(epochs, loss, "y", zorder=3, label="Training Loss")
plt.plot(epochs, val_loss, "r", zorder=3, label="Validation Loss")
plt.grid(which="major", axis="both", zorder=0)
plt.title("Training and Validation Loss")
plt.xlabel("Epochs")
plt.ylabel("Loss")
plt.legend()
plt.show()

acc = history.history["categorical_accuracy"]
val_acc = history.history["val_categorical_accuracy"]
plt.plot(epochs, acc, "y", zorder=3, label="Training Acc")
plt.plot(epochs, val_acc, "r", zorder=3, label="Validation Acc")
plt.grid(which="major", axis="both", zorder=0)
plt.title("Training and Validation Accuracy")
plt.xlabel("Epochs")
plt.ylabel("Accuracy")
plt.legend()
plt.show()

In [ ]:
res = lstm2_dense2_rd2_lr5_e1k_b16.predict(X_test)

In [ ]:
yhat = lstm2_dense2_rd2_lr5_e1k_b16.predict(X_test)
ytrue = np.argmax(y_test, axis=1).tolist()
yhat = np.argmax(yhat, axis=1).tolist()

In [ ]:
cm = confusion_matrix(y_true = ytrue, y_pred = yhat)

In [ ]:
cm_plot_labels = ["run", "walk", "skip", "jack", "jump", "pjump", "side", "wave2", "wave1", "bend"]
plot_confusion_matrix(cm = cm, classes = cm_plot_labels, title = "Confusion Matrix")

In [ ]:
y_pred = lstm2_dense2_rd2_lr5_e1k_b16.predict(X_test)
y_pred = (y_pred > 0.5)

In [ ]:
_, acc = lstm2_dense2_rd2_lr5_e1k_b16.evaluate(X_test, y_test)
print("Accuracy = ", (acc*100), " %")

In [ ]:
accuracy_score(ytrue, yhat)

In [ ]:
print(classification_report(
    ytrue,
    yhat,
    output_dict=False,
    target_names=["run", "walk", "skip", "jack", "jump", "pjump", "side", "wave2", "wave1", "bend"]
))

# Demo on a video

In [ ]:
# Probability visualisation with live side bar chart

colors = [(237, 17, 17), # walk:0 -> red
          (245, 117, 16), # run:1 -> orange
          (235, 224, 16), # jump:2 -> yellow
          (155, 235, 16), # gallop sideways:3 -> lime green
          (86, 224, 58), # bend:4 -> green
          (30, 227, 132), # one-hand wave:5 -> cyan
          (30, 224, 227), # two-hands wave:6 -> light blue
          (22, 38, 219), # jump in place:7 -> blue
          (170, 22, 219), # jumping jack:8 -> purple
          (219, 22, 104)] # skip:9 -> magenta

def prob_viz(res, actions, input_frame, colors):
    output_frame = input_frame.copy()
    
    for num, prob in enumerate(res):
        cv2.rectangle(output_frame, (0,60+num*40), (int(prob*100), 90+num*40), colors[num], -1)
        cv2.putText(output_frame, actions[num], (0, 85+num*40), cv2.FONT_HERSHEY_SIMPLEX, 1, (255,255,255), 2, cv2.LINE_AA)
    
    return output_frame

In [ ]:
# Demo

# new variable
sequence = []
sentence = []
predictions = []
threshold = 0.3

#cap = cv2.VideoCapture(0) # Webcam
cap = cv2.VideoCapture("demovideo/demovideo-dataset-zoom-flip.mp4") # Demo video

# Set mediapipe model
with mp_pose.Pose(static_image_mode=False,
                  model_complexity=1,
                  smooth_landmarks=True,
                  enable_segmentation=False,
                  smooth_segmentation=True,
                  min_detection_confidence=0.5,
                  min_tracking_confidence=0.5) as pose:
    while cap.isOpened():
        
        # Read feed
        ret, frame = cap.read()
        
        # Make detections
        image, results = mediapipe_detection(frame, pose)
        print(results)
        
        # Draw landmarks
        draw_styled_landmarks(image, results)
        
        # Prediction logic
        keypoints = extract_keypoints(results)
        sequence.append(keypoints)
        sequence = sequence[-25:]
        
        if len(sequence) == 25:
            res = model.predict(np.expand_dims(sequence, axis=0))[0]
            print(actions[np.argmax(res)])
            predictions.append(np.argmax(res))
            
            # Viz logic
            if np.unique(predictions[-10:])[0] == np.argmax(res):
                if res[np.argmax(res)] > threshold:
                    if len(sentence) > 0:
                        if actions[np.argmax(res)] != sentence[-1]:
                            sentence.append(actions[np.argmax(res)])
                    else:
                        sentence.append(actions[np.argmax(res)])
            if len(sentence) > 1:
                sentence = sentence[-1:]
                
            # Viz probabilities
            image = prob_viz(res, actions, image, colors)
            
        cv2.rectangle(image, (0,0), (720,40), (245,117,16), -1)
        cv2.putText(image, " ".join(sentence), (3,30),
                    cv2.FONT_HERSHEY_SIMPLEX, 1, (255,255,255), 2, cv2.LINE_AA)
        
        # Show to screen
        cv2.imshow("OpenCV Feed", image)
        
        #Break
        if cv2.waitKey(10) & 0xFF == ord("q"):
            break
            
    cap.release()
    cv2.destroyAllWindows()

In [ ]:
# emergency exit command
cap.release()
cv2.destroyAllWindows()